In [1]:
import pandas as pd
import nltk
nltk.download('stopwords') 
nltk.download('wordnet')
import pandas as pd
import glob
from nltk.corpus import stopwords


[nltk_data] Downloading package stopwords to
[nltk_data]     /home/jillian/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /home/jillian/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


# Creating cleaned corpus for training Doc2Vec model

In [2]:
ls_documents=[]
for file in glob.glob('Starfinder_txt/*.txt'):
    ls_documents.append(file)

In [3]:
ls_text=[]
for file in ls_documents:
    f=open(file,'r')
    ls_text.append(f.read())

In [4]:
text=pd.DataFrame(ls_text)
text.columns=['raw_text']
text['source']=['Dead_Suns_1','Signal_of_Screams_2','Dead_Suns_5','Dawn_of_Flame_5',
                   'Against_the_Aeon_Throne_2','Dead_Suns_6','Threefold_Conspiracy_2',
                   'Attack_of_the_Swarm_5','Against_the_Aeon_Throne_1','Threefold_Conspiracy_1',
                   'Dawn_of_Flame_3','Attack_of_the_Swarm_4','Attack_of_the_Swarm_6',
                   'Threefold_Conspiracy_3','Threefold_Conspiracy_4','Dead_Suns_4',
                   'Attack_of_the_Swarm_1','Threefold_Conspiracy_5','Threefold_Conspiracy_6',
                   'Attack_of_the_Swarm_2','Dead_Suns_3','Dawn_of_Flame_1','Dawn_of_Flame_4',
                   'Attack_of_the_Swarm_3','Devastation_Ark_1','Devastation_Ark_2',
                   'Devastation_Ark_3','Against_the_Aeon_Throne_3','Dawn_of_Flame_2',
                   'Signal_of_Screams_3','Signal_of_Screams_1','Dawn_of_Flame_6','Dead_Suns_2']
text=text.set_index('source')
text

raw_text
source                                                                      
Dead_Suns_1                SUNRISE MAIDEN\n\n\nTIER 3\n\nSanjaval Vagabon...
Signal_of_Screams_2        ANTUMBRA OVERSEER\n\nTIER 8\n\nLarge destroyer...
Dead_Suns_5                MODIFIED ATECH BULWARK\n\nTIER 7\n\nLarge dest...
Dawn_of_Flame_5            PROTECTOR ACCORD\n\nTIER 4\n\nSmall shuttle\nS...
Against_the_Aeon_Throne_2  VANGUARD PARAPET\t\t\n\nTIER 3\n\nMedium trans...
Dead_Suns_6                BLACKWIND ANNIHILATOR\n\nTIER 20\n\nSupercolos...
Threefold_Conspiracy_2     STEWARD BANSHEE FA FRIGATE\n\nTIER 5\n\nMedium...
Attack_of_the_Swarm_5      SUSKILLON AURORA\n\nTIER 10\n\nHuge cruiser\nS...
Against_the_Aeon_Throne_1  VANGUARD VOIDSWEEPER\t\t\n\nTIER 2\n\nMedium e...
Threefold_Conspiracy_1     SANJAVAL PALANQUIN\n\nSanjaval Spaceflight Sys...
Dawn_of_Flame_3            SUN DIVER\n\nTIER 6\n\nSmall light freighter\n...
Attack_of_the_Swarm_4      SDF RAMPART\t\t\n\nTIER 9\n\nLarge destroyer\n...
Attack_of_the_Swarm_6      EP STALWART\n\nTIER 11\n\nHuge cruiser\nSpeed ...
Threefold_Conspiracy_3     GRAY MONITOR CAPSULE\n\nTIER 4\n\nSmall shuttl...
Threefold_Conspiracy_4     ROSELIGHT ORACLE\n\nTIER 7\n\nLarge heavy frei...
Dead_Suns_4                KLOKWORX PRISM\n\nTIER 6\n\nMedium explorer\nS...
Attack_of_the_Swarm_1      TERMINUS WILD\n\nTIER 3\n\nFlux Industries Obs...
Threefold_Conspiracy_5     \nINHERITORWORKS CRUSADER\n\nTIER 9\n\nLarge d...
Threefold_Conspiracy_6     OPULOS AMBASSADOR\n\nTIER 11\n\nMedium transpo...
Attack_of_the_Swarm_2      SUSKILLON WHIP\n\nTIER 5\n\nMedium explorer\nS...
Dead_Suns_3                NEBULOR OUTFITTERS\nSTARHOPPER\n\nTIER 4\n\nMe...
Dawn_of_Flame_1            AURORA YELLOW DWARF\n\nTIER 3\n\nMedium explor...
Dawn_of_Flame_4            PYRE WOEBRINGER\n\nTIER 8\n\nHuge bulk freight...
Attack_of_the_Swarm_3      SDF D-127 DEFENSIVE CARRIER\n\nTIER 7\n\nLarge...
Devastation_Ark_1          NEW HORIZON BOREALIS\n\nTIER 9\n\nLarge Heavy ...
Devastation_Ark_2          SKYWARD GLORY\n\nTIER 10\n\nRefit Inheritorwor...
Devastation_Ark_3          MULTIFOLD INDUSTRIES HARVESTER\n\nTIER 14\n\nG...
Against_the_Aeon_Throne_3  VANGUARD REGNANT\n\nTIER 5\n\nSmall light frei...
Dawn_of_Flame_2            EXCORIATION COMBINE JEZAIL\n\nTIER 6\n\nLarge ...
Signal_of_Screams_3        \nVELSTRAC TORMENTOR\n\nTIER 9\n\nMedium trans...
Signal_of_Screams_1        RINGWORKS SENTINEL\n\nTIER 5\n\nMedium explore...
Dawn_of_Flame_6            \n\nEXCORIATION COMBINE ALCAZAR\n\n\nTIER 10\n...
Dead_Suns_2                THAUMTECH\nCAIRNCARVER\n\nTIER 2\n\nSmall ligh...

In [5]:
import re
import string

def clean_text(text):
    '''Make text lowercase, remove text in square brackets, 
    remove punctuation and remove words containing numbers, remove line breaks,
    remove words two characters or less in length, removing multiple spacings.'''
    text = text.lower()
    text = re.sub('\[.*?\]', ' ', text)
    text = re.sub('[%s]' % re.escape(string.punctuation), ' ', text)
    text = re.sub('\w*\d\w*', ' ', text)
    text = re.sub('[‘’“”…]', ' ', text)
    text = re.sub('\n', ' ', text)
    text = re.sub(r'\b\w{1,2}\b', ' ',text)
    text = re.sub(' +',' ',text)
    text= re.sub('—',' ',text)
    return text

round1 = lambda x: clean_text(x)
text_clean=pd.DataFrame(text.raw_text.apply(round1))
text_clean

raw_text
source                                                                      
Dead_Suns_1                sunrise maiden tier sanjaval vagabond medium e...
Signal_of_Screams_2        antumbra overseer tier large destroyer speed m...
Dead_Suns_5                modified atech bulwark tier large destroyer sp...
Dawn_of_Flame_5            protector accord tier small shuttle speed mane...
Against_the_Aeon_Throne_2  vanguard parapet\t\t tier medium transport spe...
Dead_Suns_6                blackwind annihilator tier supercolossal ultra...
Threefold_Conspiracy_2     steward banshee frigate tier medium explorer s...
Attack_of_the_Swarm_5      suskillon aurora tier huge cruiser speed maneu...
Against_the_Aeon_Throne_1  vanguard voidsweeper\t\t tier medium explorer ...
Threefold_Conspiracy_1     sanjaval palanquin sanjaval spaceflight system...
Dawn_of_Flame_3            sun diver tier small light freighter speed man...
Attack_of_the_Swarm_4      sdf rampart\t\t tier large destroyer speed man...
Attack_of_the_Swarm_6       stalwart tier huge cruiser speed maneuverabil...
Threefold_Conspiracy_3     gray monitor capsule tier small shuttle speed ...
Threefold_Conspiracy_4     roselight oracle tier large heavy freighter sp...
Dead_Suns_4                klokworx prism tier medium explorer speed mane...
Attack_of_the_Swarm_1      terminus wild tier flux industries observation...
Threefold_Conspiracy_5      inheritorworks crusader tier large destroyer ...
Threefold_Conspiracy_6     opulos ambassador tier medium transport speed ...
Attack_of_the_Swarm_2      suskillon whip tier medium explorer speed mane...
Dead_Suns_3                nebulor outfitters starhopper tier medium expl...
Dawn_of_Flame_1            aurora yellow dwarf tier medium explorer speed...
Dawn_of_Flame_4            pyre woebringer tier huge bulk freighter speed...
Attack_of_the_Swarm_3      sdf defensive carrier tier large heavy freight...
Devastation_Ark_1          new horizon borealis tier large heavy freighte...
Devastation_Ark_2          skyward glory tier refit inheritorworks laserl...
Devastation_Ark_3          multifold industries harvester tier gargantuan...
Against_the_Aeon_Throne_3  vanguard regnant tier small light freighter sp...
Dawn_of_Flame_2            excoriation combine jezail tier large destroye...
Signal_of_Screams_3         velstrac tormentor tier medium transport spee...
Signal_of_Screams_1        ringworks sentinel tier medium explorer speed ...
Dawn_of_Flame_6             excoriation combine alcazar tier huge cruiser...
Dead_Suns_2                thaumtech cairncarver tier small light freight...

In [6]:
#removing stopwords
stopwords= stopwords.words('english')
new_stopwords=['statistics','tactics','ecology','bulk','defense','offense','treasure',
               'mission','pcs','starfinder','starfinders'] 
stopwords.extend(new_stopwords)
text_clean['no_stop']=text_clean['raw_text'].apply(lambda x: ' '.join(
    [word for word in x.split()if word not in (stopwords)]))

In [7]:
text_clean.no_stop.iloc[0]

'sunrise maiden tier sanjaval vagabond medium explorer speed maneuverability good turn drift shields light forward port starboard aft attack forward gyrolaser attack port light laser cannon attack starboard light laser cannon attack aft flak thrower attack turret light particle beam power core pulse green pcu drift engine signal basic systems basic mid range sensors crew quarters good extra light weapon mount aft armor defenses duonode computer tier artificial personality upgrade expansion bays cargo holds escape pods recreation suite hac gym modifiers checks per round computers piloting complement – sanjaval spaceflight systems vagabond class multipurpose light transport freighter versatile workhorse reputation durability reliability service years vagabonds still regularly used throughout pact worlds cargo haulers smuggling ships exploratory survey vessels crew six standard complement vagabond ship coordinated control interface double redundancies critical systems designed allow singl

In [8]:
#splitting documents into words
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
#tokenize and tag text
docs = [TaggedDocument(doc.split(' '), [i]) 
        for i, doc in enumerate(text_clean.no_stop)]
docs

[TaggedDocument(words=['sunrise', 'maiden', 'tier', 'sanjaval', 'vagabond', 'medium', 'explorer', 'speed', 'maneuverability', 'good', 'turn', 'drift', 'shields', 'light', 'forward', 'port', 'starboard', 'aft', 'attack', 'forward', 'gyrolaser', 'attack', 'port', 'light', 'laser', 'cannon', 'attack', 'starboard', 'light', 'laser', 'cannon', 'attack', 'aft', 'flak', 'thrower', 'attack', 'turret', 'light', 'particle', 'beam', 'power', 'core', 'pulse', 'green', 'pcu', 'drift', 'engine', 'signal', 'basic', 'systems', 'basic', 'mid', 'range', 'sensors', 'crew', 'quarters', 'good', 'extra', 'light', 'weapon', 'mount', 'aft', 'armor', 'defenses', 'duonode', 'computer', 'tier', 'artificial', 'personality', 'upgrade', 'expansion', 'bays', 'cargo', 'holds', 'escape', 'pods', 'recreation', 'suite', 'hac', 'gym', 'modifiers', 'checks', 'per', 'round', 'computers', 'piloting', 'complement', '–', 'sanjaval', 'spaceflight', 'systems', 'vagabond', 'class', 'multipurpose', 'light', 'transport', 'freighte

In [9]:
#model training
model = Doc2Vec(docs, vector_size=100, window=5, min_count=2, workers=8, epochs = 20)
model.wv.most_similar('gragant')


[('lestana', 0.8702516555786133),
 ('innovations', 0.8419818878173828),
 ('eclipse', 0.835953950881958),
 ('kaeon', 0.8310360908508301),
 ('corrupting', 0.8045966029167175),
 ('assistants', 0.7976654767990112),
 ('shadow', 0.7824560403823853),
 ('sinister', 0.7815288305282593),
 ('strain', 0.7743355631828308),
 ('rhyse', 0.7700376510620117)]

# Looking at Characters

In [27]:
model.wv.most_similar('gragant',topn=50)

[('lestana', 0.8847664594650269),
 ('eclipse', 0.8429324626922607),
 ('innovations', 0.8323938846588135),
 ('kaeon', 0.8134812116622925),
 ('nightmares', 0.80709308385849),
 ('corrupting', 0.7743551731109619),
 ('shadow', 0.7692784070968628),
 ('rhyse', 0.7654408812522888),
 ('trapping', 0.759834885597229),
 ('transmitters', 0.7542369961738586),
 ('eventually', 0.7506212592124939),
 ('reality', 0.74185711145401),
 ('sinister', 0.739331066608429),
 ('corruption', 0.7365762591362),
 ('carnage', 0.7340807914733887),
 ('god', 0.7311336398124695),
 ('experiments', 0.7308279275894165),
 ('pain', 0.7292070388793945),
 ('changed', 0.7274542450904846),
 ('transforming', 0.7211519479751587),
 ('strain', 0.7210179567337036),
 ('entity', 0.7164530754089355),
 ('verces', 0.7119656801223755),
 ('father', 0.7118355631828308),
 ('performed', 0.7117050886154175),
 ('patron', 0.7113041877746582),
 ('clinical', 0.7108325958251953),
 ('became', 0.7085528373718262),
 ('slaughter', 0.7045681476593018),
 ('p

In [28]:
model.wv.most_similar('serovox',topn=50)

[('admiral', 0.8746424913406372),
 ('supremacy', 0.8656567931175232),
 ('honor', 0.8561683297157288),
 ('upcoming', 0.8528773188591003),
 ('effort', 0.825427234172821),
 ('decided', 0.8209723830223083),
 ('secretly', 0.8159298896789551),
 ('insurgents', 0.8096858263015747),
 ('timely', 0.8096057176589966),
 ('erio', 0.8018630146980286),
 ('audacious', 0.8013808727264404),
 ('ultimately', 0.8009191751480103),
 ('fruition', 0.799293041229248),
 ('employers', 0.7980539798736572),
 ('grave', 0.7967096567153931),
 ('horrified', 0.7873483300209045),
 ('imprison', 0.7835315465927124),
 ('desperately', 0.7778000831604004),
 ('informed', 0.777356743812561),
 ('outright', 0.7756129503250122),
 ('employer', 0.7748363614082336),
 ('destined', 0.7739109396934509),
 ('fanatics', 0.7727396488189697),
 ('conflict', 0.7726079225540161),
 ('arrested', 0.7720906734466553),
 ('contacted', 0.7700921893119812),
 ('honorable', 0.7691787481307983),
 ('duplicity', 0.7681295871734619),
 ('convinced', 0.76686668

In [29]:
model.wv.most_similar('khaim',topn=50)

[('general', 0.8732285499572754),
 ('hags', 0.8446137309074402),
 ('efreet', 0.8344982862472534),
 ('imprisoned', 0.8307302594184875),
 ('conquer', 0.8305869102478027),
 ('malikah', 0.8139427900314331),
 ('merits', 0.8025773763656616),
 ('cauldron', 0.802514374256134),
 ('asanatown', 0.7977421283721924),
 ('helped', 0.7963432669639587),
 ('inhabitants', 0.7917298674583435),
 ('uzmat', 0.7901170253753662),
 ('favoritism', 0.7880355715751648),
 ('coven', 0.7846895456314087),
 ('employer', 0.7810327410697937),
 ('plans', 0.7764246463775635),
 ('proved', 0.7756396532058716),
 ('invading', 0.7711755037307739),
 ('kam', 0.7694441080093384),
 ('rebuilds', 0.7691294550895691),
 ('effort', 0.7647405862808228),
 ('origins', 0.7643694281578064),
 ('chose', 0.7613892555236816),
 ('goals', 0.7611883878707886),
 ('fivefold', 0.7603650093078613),
 ('ognea', 0.7598334550857544),
 ('anassanois', 0.7585041522979736),
 ('supremacy', 0.7583761215209961),
 ('compile', 0.7583649158477783),
 ('boarded', 0.75

In [30]:
model.wv.most_similar('ulivestra',topn=50)

[('sardat', 0.959697961807251),
 ('zolan', 0.9156779050827026),
 ('bureaucracy', 0.8593262434005737),
 ('nobility', 0.8559276461601257),
 ('ivsc', 0.8278065323829651),
 ('fabled', 0.8109374046325684),
 ('meanwhile', 0.8089398145675659),
 ('purchased', 0.8015363812446594),
 ('royal', 0.7929799556732178),
 ('parept', 0.7923426628112793),
 ('vestiges', 0.785845160484314),
 ('noble', 0.7727365493774414),
 ('brainwashed', 0.7726688385009766),
 ('cedona', 0.772148609161377),
 ('ameondria', 0.7720516920089722),
 ('goodhearted', 0.7677128314971924),
 ('azlanti', 0.7667350769042969),
 ('venture', 0.7652602195739746),
 ('entanglements', 0.7625879049301147),
 ('informed', 0.7595649361610413),
 ('gevalarsk', 0.7585853934288025),
 ('imperial', 0.7563589811325073),
 ('skraelin', 0.7529853582382202),
 ('technically', 0.7499831318855286),
 ('losifaran', 0.7469115853309631),
 ('ambitious', 0.7468088865280151),
 ('branch', 0.7457646727561951),
 ('non', 0.7453241348266602),
 ('member', 0.7419928312301636

In [31]:
model.wv.most_similar('najiri',topn=50)

[('commander', 0.9136096239089966),
 ('hadiya', 0.8258785009384155),
 ('eskolar', 0.8244888186454773),
 ('encourages', 0.7928041815757751),
 ('ognea', 0.7846953868865967),
 ('resourceful', 0.7808049917221069),
 ('report', 0.7797698974609375),
 ('rescued', 0.7672051191329956),
 ('refugees', 0.7668794989585876),
 ('jalusann', 0.7656174898147583),
 ('cavalier', 0.7567649483680725),
 ('town', 0.7547940015792847),
 ('mentor', 0.7542760372161865),
 ('getting', 0.7492341995239258),
 ('sdf', 0.7462561130523682),
 ('commit', 0.745986819267273),
 ('regarding', 0.7455824613571167),
 ('informing', 0.7435440421104431),
 ('explains', 0.7402873635292053),
 ('orders', 0.7385957837104797),
 ('convey', 0.7374376058578491),
 ('tells', 0.7355654835700989),
 ('missions', 0.7343766689300537),
 ('shortly', 0.7322499752044678),
 ('befriend', 0.7299824953079224),
 ('assigned', 0.729100227355957),
 ('glad', 0.728656530380249),
 ('collegial', 0.7284047603607178),
 ('shavesko', 0.7272263765335083),
 ('contacts', 

# Comparison of similarity between antagonist and non-antagonist characters

In [32]:
import itertools
villians=['gragant','serovox','khaim','tahomen','godhost','anacia','reda','chendwen','thisskt',
         'candlerime','vavex','vheiransch','konsuvias','nirin','pazzoedioth','xiello','jalkashti',
         'olaraja','sharu','iolastrila','grasilex','skraelin','oliviana','nikkost','chamas',
         'vadak','tola','throsh','dosc','gallask','jabaxa','salask','hybeki','kaeon']
good_guys=['najiri','chiskisk','xych','jaldamarrak','loachwurt','xelonan','etchiax','hescamu',
           'jadvata','tuvah','allicyn','cinneka','ognea','kahore','eisyfina',
           'klendalikh','kalthlo','madelon','aibretta','cedona','erio','nib','pahdric','lurian',
           'taza','otlo','beran','muhali','solstarni','waneda','tzayl','quillius','lominn','veyla']

def character_similarities(villians,good_guys):
    """Lists type of similarity pairing, members of pairing, and level of similarity
    pairs are villians/good guys, villian/villian, and good guy/good guy"""
    sim=[]
    for i in villians:
        for j in good_guys:
            sim.append(('v-g',i,j,model.wv.similarity(i,j)))
    for i,j in list(itertools.combinations(villians,2)):
        sim.append(('v-v',i,j,model.wv.similarity(i,j)))
    for i,j in list(itertools.combinations(good_guys,2)):
        sim.append(('g-g',i,j,model.wv.similarity(i,j)))  
    return sim
ch_sim=character_similarities(villians,good_guys)


In [33]:
#creating dataframe for ease of understanding
#could use this as starting point for further analysis, find characters that are very similar
# then look into how they are similar
sim_df=pd.DataFrame(ch_sim, columns=['Pairing Type','character name','paired character','similarity score'])
sim_df['Pairing Type']=sim_df['Pairing Type'].replace(['v-g','v-v','g-g'],['villian-good','villian-villian','good-good'])
sim_df

Pairing Type character name paired character  similarity score
0     villian-good        gragant           najiri          0.251456
1     villian-good        gragant         chiskisk          0.531236
2     villian-good        gragant             xych          0.456426
3     villian-good        gragant      jaldamarrak          0.411773
4     villian-good        gragant        loachwurt          0.522326
...            ...            ...              ...               ...
2273     good-good          tzayl           lominn          0.611749
2274     good-good          tzayl            veyla          0.672478
2275     good-good       quillius           lominn          0.103247
2276     good-good       quillius            veyla          0.380926
2277     good-good         lominn            veyla          0.644942

[2278 rows x 4 columns]

In [36]:
#one of these characters is not a villian
model.wv.doesnt_match(['gragant','khaim','fulson','serovox'])

'fulson'

# Testing Word Embedding Visualization
Not very happy with this currently, something to work on and explore in the future

In [20]:
def append_list(sim_words, words):
    
    list_of_words = []
    
    for i in range(len(sim_words)):
        
        sim_words_list = list(sim_words[i])
        sim_words_list.append(words)
        sim_words_tuple = tuple(sim_words_list)
        list_of_words.append(sim_words_tuple)
        
    return list_of_words

input_word = 'gragant,serovox'
user_input = [x.strip() for x in input_word.split(',')]
result_word = []
    
for words in user_input:
    
        sim_words = model.wv.most_similar(words, topn = 3)
        sim_words = append_list(sim_words, words)
            
        result_word.extend(sim_words)
    
similar_word = [word[0] for word in result_word]
similarity = [word[1] for word in result_word] 
similar_word.extend(user_input)
labels = [word[2] for word in result_word]
label_dict = dict([(y,x+1) for x,y in enumerate(set(labels))])
color_map = [label_dict[x] for x in labels]

In [21]:
import plotly
import numpy as np
import plotly.graph_objs as go
from sklearn.decomposition import PCA

def display_pca_scatterplot_2D(model, user_input=None, words=None, label=None, color_map=None, topn=3, sample=10):

    if words == None:
        if sample > 0:
            words = np.random.choice(list(model.vocab.keys()), sample)
        else:
            words = [ word for word in model.vocab ]
    
    word_vectors = np.array([model[w] for w in words])
    
    two_dim = PCA(random_state=0).fit_transform(word_vectors)[:,:2]

    data = []
    count = 0
    
    for i in range (len(user_input)):

                trace = go.Scatter(
                    x = two_dim[count:count+topn,0], 
                    y = two_dim[count:count+topn,1],  
                    text = words[count:count+topn],
                    name = user_input[i],
                    textposition = "top center",
                    textfont_size = 20,
                    mode = 'markers+text',
                    marker = {
                        'size': 10,
                        'opacity': 0.8,
                        'color': 2
                    }
       
                )
            
                data.append(trace)
                count = count+topn

    trace_input = go.Scatter(
                    x = two_dim[count:,0], 
                    y = two_dim[count:,1],  
                    text = words[count:],
                    name = 'input words',
                    textposition = "top center",
                    textfont_size = 20,
                    mode = 'markers+text',
                    marker = {
                        'size': 10,
                        'opacity': 1,
                        'color': 'black'
                    }
                    )
            
    data.append(trace_input)
    
# Configure the layout

    layout = go.Layout(
        margin = {'l': 0, 'r': 0, 'b': 0, 't': 0},
        showlegend=True,
        legend=dict(
        x=1,
        y=0.5,
        font=dict(
            family="Courier New",
            size=25,
            color="black"
        )),
        font = dict(
            family = " Courier New ",
            size = 15),
        autosize = False,
        width = 1000,
        height = 1000
        )


    plot_figure = go.Figure(data = data, layout = layout)
    plot_figure.show()
    
display_pca_scatterplot_2D(model, user_input, similar_word, labels, color_map)